In [1]:
import os
import numpy as np
import cv2
import matplotlib.pyplot as plt
import argparse
import matplotlib.pyplot as plt
import albumentations
import segmentation_models_pytorch as smp
from segmentation_models_pytorch import utils as smp_utils
import torch
import torch.nn.functional as F
from tqdm import tqdm as tqdm
import sys
from torch.utils.data import DataLoader
import math
from PIL import Image
Image.MAX_IMAGE_PIXELS = None
import glob
import rasterio
import json
import re
import tifffile
from skimage import measure
from rasterio.features import shapes
torch.__version__

C:\Users\AhmadWaseem\.conda\envs\pd-seg\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


'1.9.1+cpu'

In [2]:
#////////////////////////Pre Processing\\\\\\\\\\\\\\\\\\\\\\\\
def get_preprocessing(preprocessing_fn):
    """Construct preprocessing transform

    Args:
        preprocessing_fn (callbale): data normalization function
            (can be specific for each pretrained neural network)
    Return:
        transform: albumentations.Compose

    """

    _transform = [
        albumentations.Lambda(image=preprocessing_fn),
    ]
    return albumentations.Compose(_transform)



In [3]:
#//////////////////////// Evaluate on Large Tiff File(s) \\\\\\\\\\\\\\\\\\\\\\\\
#input_imgs = os.path.join(data_dir, 'tiff_images') # Input the path to tiff images
input_imgs = r"C:\Users\AhmadWaseem\Desktop\bhalli\PD-Seg Work\datasets for training - 20Z\tiff files\2017\2017 reproject.tif"
model_path = r"C:\Users\AhmadWaseem\Desktop\bhalli\PD-Seg Work\model v6 - DL 20Z - TS1024\model h5"
output_dir = r"C:\Users\AhmadWaseem\Desktop\bhalli\PD-Seg Work\model v6 - DL 20Z - TS1024\output"

ENCODER = 'resnet50'
ENCODER_WEIGHTS = 'imagenet'

target_size = (1024, 1024)
padding_pixels = (100, 100)
padding_value = 0
downsampling_factor = 1
DEVICE = torch.device("cuda" if torch.cuda.is_available() else "cpu")
PIX_VALUE_MAX = 255    # The max data value we have
PIX_VALUE_MAX_REQ = 255 # The max data value we need

model = torch.load(os.path.join(model_path, 'best_model.h5'), map_location=DEVICE)
model.eval()
imgs = [file for file in glob.glob(input_imgs) if file.endswith('.tif')]
print(imgs)
assert len(imgs) > 0, "The number of images equal to zero"

#num_processes = 1
print("Running on {} images".format(len(imgs)))# using {} parallel processes".format(len(imgs), num_processes))

# pos = len(input_imgs.split('*')[0]) #Related to naming of output file

#args = [[img, DEVICE, model, args.output_dir] for img in imgs]

'''
if num_processes > 1:
    p = mlt.Pool(num_processes)
    (p.map(process, args))
    p.close()
else:
    for arg in args:
        process(arg)'''

#img_path, device, model, output_dir, pos = args[0]

for img_path in imgs:
    #img_path = imgs[0]
    file_name = os.path.split(img_path)[-1].split('.')[0]
    print("Running for {}".format(file_name))

    if not os.path.exists(output_dir):
        os.makedirs(output_dir)

    save_path = os.path.join(output_dir, file_name + "_preds.npy")
    img = np.transpose(rasterio.open(img_path).read(), (1, 2, 0))
#     max_value = np.iinfo(img.dtype).max
    print("Actual Image Size: {}".format(img.shape))

    #Define k_x, k_y to define 'useful' portion, since we are taking patches with overlapping area.
    k_y = target_size[0] - 2 * padding_pixels[0]
    k_x = target_size[1] - 2 * padding_pixels[1]

    # First padding: To make divisible by k
    cols = (math.ceil(img.shape[0]/k_y))
    rows = (math.ceil(img.shape[1]/k_x))

    pad_bottom = cols*k_y - img.shape[0]   #pixels to add in y direction
    pad_right = rows*k_x - img.shape[1]    #pixels to add in x direction
    if pad_bottom > 0 or pad_right > 0:
        print("Running cv2 padding..")
        img = cv2.copyMakeBorder(img, 0, pad_bottom, 0, pad_right, cv2.BORDER_CONSTANT, value=padding_value)
    print("Image Size after making divisible by ({}, {}): {}".format(k_x, k_y, img.shape))

    output_image = np.zeros((int(img.shape[0]*downsampling_factor), int(img.shape[1]*downsampling_factor)), dtype=np.uint8) * 255
    print("Size of output image after downsampling factor of {}: {}".format(downsampling_factor, output_image.shape))

    # Second Padding: To add boundary padding pixels
    img = cv2.copyMakeBorder(img, padding_pixels[0], padding_pixels[0], padding_pixels[1], 
                             padding_pixels[1], cv2.BORDER_CONSTANT, value=padding_value)
    print("Image Size after adding ({}, {}) boundary pixels: {}".format(padding_pixels[0], padding_pixels[0], img.shape))

    # Load pre-processing function
    preprocessing_fn = smp.encoders.get_preprocessing_fn(ENCODER, ENCODER_WEIGHTS)
    preprocessing = get_preprocessing(preprocessing_fn)

    total_patches = rows*cols
    print("Total {} patches for the given image {}".format(rows*cols, file_name))
    for y_idx in range(cols):
        y1 = y_idx*k_y + padding_pixels[0]
        y2 = y1 + k_y
#         if y_idx <= 0:
#             continue
        for x_idx in range(rows):
            x1 = x_idx*k_x + padding_pixels[1]
            x2 = x1 + k_x
            patch_number = y_idx*rows + x_idx + 1

            img_crop = img[y1-padding_pixels[0]: y2 + padding_pixels[0], x1 - padding_pixels[1]: x2 + padding_pixels[1]]
            print("Patch {} of {}: [{}:{}, {}:{}]".format(patch_number, total_patches, y1-padding_pixels[0],
                                                          y2 + padding_pixels[0], x1 - padding_pixels[1],
                                                          x2 + padding_pixels[1]), end =" ")
            
            img_crop = ((img_crop/PIX_VALUE_MAX)*(PIX_VALUE_MAX_REQ)).astype(np.uint8)
#             plt.subplot(1, 2, 1)
#             plt.imshow(img_crop)
#             print(img_crop.max())
            sample = preprocessing(image=img_crop)
            image = cv2.resize(sample['image'], 
                               (int(downsampling_factor * target_size[0]),
                                int(downsampling_factor * target_size[1])),
                               interpolation = cv2.INTER_AREA)
#             plt.subplot(1, 2, 2)
#             plt.imshow(denormalize(image))
#             plt.show()
#             print(image.max())
            x_tensor = torch.Tensor(image).permute(2, 0, 1).to(DEVICE).unsqueeze(0)
#             image = np.transpose(image, (2, 0, 1))#.astype('float32')
#             x_tensor = torch.from_numpy(image).to(DEVICE).unsqueeze(0)
            with torch.no_grad():
                pred_mask = model(x_tensor)
            pr_mask = pred_mask.squeeze()
            pr_mask = pr_mask.detach().squeeze().cpu().numpy().round()

            patch = pr_mask[int(downsampling_factor * padding_pixels[0]) : int(downsampling_factor * (target_size[0] - padding_pixels[0])),
                            int(downsampling_factor * padding_pixels[1]) : int(downsampling_factor * (target_size[1] - padding_pixels[1]))]
#             print(",Output: [{}:{}, {}:{}]".format(int(downsampling_factor*(y_idx*k_y)), int(downsampling_factor*(y_idx*k_y + k_y)),
#                                                    int(downsampling_factor*(x_idx*k_x)), int(downsampling_factor*(x_idx*k_x + k_x)),
#                                                    end =" "))
            output_image[int(downsampling_factor*(y_idx*k_y)): int(downsampling_factor*(y_idx*k_y + k_y)),
                           int(downsampling_factor*(x_idx*k_x)): int(downsampling_factor*(x_idx*k_x + k_x))] = patch
            print("..... Done!")
#         break


output_image = output_image[:output_image.shape[0] - int(downsampling_factor * pad_bottom),
                            :output_image.shape[1] - int(downsampling_factor * pad_right)]
print("Final shape of downsampled output image: {}".format(output_image.shape))

np.save(save_path, output_image)

img_array = np.load(r'C:\Users\AhmadWaseem\Desktop\bhalli\PD-Seg Work\model v6 - DL 20Z - TS1024\output\output_preds.npy')
tifffile.imwrite(r'C:\Users\AhmadWaseem\Desktop\bhalli\PD-Seg Work\model v6 - DL 20Z - TS1024\outputs\output_preds.tiff',img_array)
print("Completed!")

['C:\\Users\\AhmadWaseem\\Desktop\\bhalli\\PD-Seg Work\\datasets for training - 20Z\\tiff files\\2017\\2017 reproject.tif']
Running on 1 images
Running for 2017 reproject
Actual Image Size: (210794, 228416, 3)
Running cv2 padding..
Image Size after making divisible by (824, 824): (210944, 229072, 3)
Size of output image after downsampling factor of 1: (210944, 229072)
Image Size after adding (100, 100) boundary pixels: (211144, 229272, 3)
Total 71168 patches for the given image 2017 reproject
Patch 1 of 71168: [0:1024, 0:1024] ..... Done!
Patch 2 of 71168: [0:1024, 824:1848] ..... Done!
Patch 3 of 71168: [0:1024, 1648:2672] ..... Done!
Patch 4 of 71168: [0:1024, 2472:3496] ..... Done!
Patch 5 of 71168: [0:1024, 3296:4320] ..... Done!
Patch 6 of 71168: [0:1024, 4120:5144] ..... Done!
Patch 7 of 71168: [0:1024, 4944:5968] ..... Done!
Patch 8 of 71168: [0:1024, 5768:6792] ..... Done!
Patch 9 of 71168: [0:1024, 6592:7616] ..... Done!
Patch 10 of 71168: [0:1024, 7416:8440] ..... Done!
Patch

Patch 145 of 71168: [0:1024, 118656:119680] ..... Done!
Patch 146 of 71168: [0:1024, 119480:120504] ..... Done!
Patch 147 of 71168: [0:1024, 120304:121328] ..... Done!
Patch 148 of 71168: [0:1024, 121128:122152] ..... Done!
Patch 149 of 71168: [0:1024, 121952:122976] ..... Done!
Patch 150 of 71168: [0:1024, 122776:123800] ..... Done!
Patch 151 of 71168: [0:1024, 123600:124624] ..... Done!
Patch 152 of 71168: [0:1024, 124424:125448] ..... Done!
Patch 153 of 71168: [0:1024, 125248:126272] ..... Done!
Patch 154 of 71168: [0:1024, 126072:127096] ..... Done!
Patch 155 of 71168: [0:1024, 126896:127920] ..... Done!
Patch 156 of 71168: [0:1024, 127720:128744] ..... Done!
Patch 157 of 71168: [0:1024, 128544:129568] ..... Done!
Patch 158 of 71168: [0:1024, 129368:130392] ..... Done!
Patch 159 of 71168: [0:1024, 130192:131216] ..... Done!
Patch 160 of 71168: [0:1024, 131016:132040] ..... Done!
Patch 161 of 71168: [0:1024, 131840:132864] ..... Done!
Patch 162 of 71168: [0:1024, 132664:133688] ....

Patch 292 of 71168: [824:1848, 10712:11736] ..... Done!
Patch 293 of 71168: [824:1848, 11536:12560] ..... Done!
Patch 294 of 71168: [824:1848, 12360:13384] ..... Done!
Patch 295 of 71168: [824:1848, 13184:14208] ..... Done!
Patch 296 of 71168: [824:1848, 14008:15032] ..... Done!
Patch 297 of 71168: [824:1848, 14832:15856] ..... Done!
Patch 298 of 71168: [824:1848, 15656:16680] ..... Done!
Patch 299 of 71168: [824:1848, 16480:17504] ..... Done!
Patch 300 of 71168: [824:1848, 17304:18328] ..... Done!
Patch 301 of 71168: [824:1848, 18128:19152] ..... Done!
Patch 302 of 71168: [824:1848, 18952:19976] ..... Done!
Patch 303 of 71168: [824:1848, 19776:20800] ..... Done!
Patch 304 of 71168: [824:1848, 20600:21624] ..... Done!
Patch 305 of 71168: [824:1848, 21424:22448] ..... Done!
Patch 306 of 71168: [824:1848, 22248:23272] ..... Done!
Patch 307 of 71168: [824:1848, 23072:24096] ..... Done!
Patch 308 of 71168: [824:1848, 23896:24920] ..... Done!
Patch 309 of 71168: [824:1848, 24720:25744] ....

Patch 437 of 71168: [824:1848, 130192:131216] ..... Done!
Patch 438 of 71168: [824:1848, 131016:132040] ..... Done!
Patch 439 of 71168: [824:1848, 131840:132864] ..... Done!
Patch 440 of 71168: [824:1848, 132664:133688] ..... Done!
Patch 441 of 71168: [824:1848, 133488:134512] ..... Done!
Patch 442 of 71168: [824:1848, 134312:135336] ..... Done!
Patch 443 of 71168: [824:1848, 135136:136160] ..... Done!
Patch 444 of 71168: [824:1848, 135960:136984] ..... Done!
Patch 445 of 71168: [824:1848, 136784:137808] ..... Done!
Patch 446 of 71168: [824:1848, 137608:138632] ..... Done!
Patch 447 of 71168: [824:1848, 138432:139456] ..... Done!
Patch 448 of 71168: [824:1848, 139256:140280] ..... Done!
Patch 449 of 71168: [824:1848, 140080:141104] ..... Done!
Patch 450 of 71168: [824:1848, 140904:141928] ..... Done!
Patch 451 of 71168: [824:1848, 141728:142752] ..... Done!
Patch 452 of 71168: [824:1848, 142552:143576] ..... Done!
Patch 453 of 71168: [824:1848, 143376:144400] ..... Done!
Patch 454 of 7

Patch 579 of 71168: [1648:2672, 18128:19152] ..... Done!
Patch 580 of 71168: [1648:2672, 18952:19976] ..... Done!
Patch 581 of 71168: [1648:2672, 19776:20800] ..... Done!
Patch 582 of 71168: [1648:2672, 20600:21624] ..... Done!
Patch 583 of 71168: [1648:2672, 21424:22448] ..... Done!
Patch 584 of 71168: [1648:2672, 22248:23272] ..... Done!
Patch 585 of 71168: [1648:2672, 23072:24096] ..... Done!
Patch 586 of 71168: [1648:2672, 23896:24920] ..... Done!
Patch 587 of 71168: [1648:2672, 24720:25744] ..... Done!
Patch 588 of 71168: [1648:2672, 25544:26568] ..... Done!
Patch 589 of 71168: [1648:2672, 26368:27392] ..... Done!
Patch 590 of 71168: [1648:2672, 27192:28216] ..... Done!
Patch 591 of 71168: [1648:2672, 28016:29040] ..... Done!
Patch 592 of 71168: [1648:2672, 28840:29864] ..... Done!
Patch 593 of 71168: [1648:2672, 29664:30688] ..... Done!
Patch 594 of 71168: [1648:2672, 30488:31512] ..... Done!
Patch 595 of 71168: [1648:2672, 31312:32336] ..... Done!
Patch 596 of 71168: [1648:2672,

...

Patch 70663 of 71168: [209296:210320, 41200:42224] ..... Done!
Patch 70664 of 71168: [209296:210320, 42024:43048] ..... Done!
Patch 70665 of 71168: [209296:210320, 42848:43872] ..... Done!
Patch 70666 of 71168: [209296:210320, 43672:44696] ..... Done!
Patch 70667 of 71168: [209296:210320, 44496:45520] ..... Done!
Patch 70668 of 71168: [209296:210320, 45320:46344] ..... Done!
Patch 70669 of 71168: [209296:210320, 46144:47168] ..... Done!
Patch 70670 of 71168: [209296:210320, 46968:47992] ..... Done!
Patch 70671 of 71168: [209296:210320, 47792:48816] ..... Done!
Patch 70672 of 71168: [209296:210320, 48616:49640] ..... Done!
Patch 70673 of 71168: [209296:210320, 49440:50464] ..... Done!
Patch 70674 of 71168: [209296:210320, 50264:51288] ..... Done!
Patch 70675 of 71168: [209296:210320, 51088:52112] ..... Done!
Patch 70676 of 71168: [209296:210320, 51912:52936] ..... Done!
Patch 70677 of 71168: [209296:210320, 52736:53760] ..... Done!
Patch 70678 of 71168: [209296:210320, 53560:54584] ....

Patch 70791 of 71168: [209296:210320, 146672:147696] ..... Done!
Patch 70792 of 71168: [209296:210320, 147496:148520] ..... Done!
Patch 70793 of 71168: [209296:210320, 148320:149344] ..... Done!
Patch 70794 of 71168: [209296:210320, 149144:150168] ..... Done!
Patch 70795 of 71168: [209296:210320, 149968:150992] ..... Done!
Patch 70796 of 71168: [209296:210320, 150792:151816] ..... Done!
Patch 70797 of 71168: [209296:210320, 151616:152640] ..... Done!
Patch 70798 of 71168: [209296:210320, 152440:153464] ..... Done!
Patch 70799 of 71168: [209296:210320, 153264:154288] ..... Done!
Patch 70800 of 71168: [209296:210320, 154088:155112] ..... Done!
Patch 70801 of 71168: [209296:210320, 154912:155936] ..... Done!
Patch 70802 of 71168: [209296:210320, 155736:156760] ..... Done!
Patch 70803 of 71168: [209296:210320, 156560:157584] ..... Done!
Patch 70804 of 71168: [209296:210320, 157384:158408] ..... Done!
Patch 70805 of 71168: [209296:210320, 158208:159232] ..... Done!
Patch 70806 of 71168: [20

Patch 70918 of 71168: [210120:211144, 22248:23272] ..... Done!
Patch 70919 of 71168: [210120:211144, 23072:24096] ..... Done!
Patch 70920 of 71168: [210120:211144, 23896:24920] ..... Done!
Patch 70921 of 71168: [210120:211144, 24720:25744] ..... Done!
Patch 70922 of 71168: [210120:211144, 25544:26568] ..... Done!
Patch 70923 of 71168: [210120:211144, 26368:27392] ..... Done!
Patch 70924 of 71168: [210120:211144, 27192:28216] ..... Done!
Patch 70925 of 71168: [210120:211144, 28016:29040] ..... Done!
Patch 70926 of 71168: [210120:211144, 28840:29864] ..... Done!
Patch 70927 of 71168: [210120:211144, 29664:30688] ..... Done!
Patch 70928 of 71168: [210120:211144, 30488:31512] ..... Done!
Patch 70929 of 71168: [210120:211144, 31312:32336] ..... Done!
Patch 70930 of 71168: [210120:211144, 32136:33160] ..... Done!
Patch 70931 of 71168: [210120:211144, 32960:33984] ..... Done!
Patch 70932 of 71168: [210120:211144, 33784:34808] ..... Done!
Patch 70933 of 71168: [210120:211144, 34608:35632] ....

Patch 71047 of 71168: [210120:211144, 128544:129568] ..... Done!
Patch 71048 of 71168: [210120:211144, 129368:130392] ..... Done!
Patch 71049 of 71168: [210120:211144, 130192:131216] ..... Done!
Patch 71050 of 71168: [210120:211144, 131016:132040] ..... Done!
Patch 71051 of 71168: [210120:211144, 131840:132864] ..... Done!
Patch 71052 of 71168: [210120:211144, 132664:133688] ..... Done!
Patch 71053 of 71168: [210120:211144, 133488:134512] ..... Done!
Patch 71054 of 71168: [210120:211144, 134312:135336] ..... Done!
Patch 71055 of 71168: [210120:211144, 135136:136160] ..... Done!
Patch 71056 of 71168: [210120:211144, 135960:136984] ..... Done!
Patch 71057 of 71168: [210120:211144, 136784:137808] ..... Done!
Patch 71058 of 71168: [210120:211144, 137608:138632] ..... Done!
Patch 71059 of 71168: [210120:211144, 138432:139456] ..... Done!
Patch 71060 of 71168: [210120:211144, 139256:140280] ..... Done!
Patch 71061 of 71168: [210120:211144, 140080:141104] ..... Done!
Patch 71062 of 71168: [21

FileNotFoundError: [Errno 2] No such file or directory: 'C:\\Users\\AhmadWaseem\\Desktop\\bhalli\\PD-Seg Work\\model v6 - DL 20Z - TS1024\\output\\output_preds.npy'

In [7]:
img_array = np.load(r'C:\Users\AhmadWaseem\Desktop\bhalli\PD-Seg Work\model v6 - DL 20Z - TS1024\output\2017 reproject_preds.npy')
tifffile.imwrite(r'C:\Users\AhmadWaseem\Desktop\bhalli\PD-Seg Work\model v6 - DL 20Z - TS1024\output\2017 reproject_preds.tiff',img_array)
print("Completed!")

Completed!


In [9]:
# #//////////////////////// Functions for Evaluation \\\\\\\\\\\\\\\\\\\\\\\\

# def save_as_csv(out_path, contours, filename):
#     out_path = os.path.join(out_path, filename+'_polygons.csv')
#     print('save csv: %s, npoly = %d' % (out_path, len(contours)))
#     fw = open(out_path, 'w')
#     fw.write("filename,id,Geometry\n")
#     for j, contour in enumerate(contours):
#         polygon_str = re.sub(r"[\[\]]", '', ",".join(map(str, contour)))
#         #polygon_str = polygon_str.replace(". ", ' ')
#         #polygon_str = polygon_str.replace(".,", ',')
#         #polygon_str = re.sub(r" {2,}", ' ', polygon_str)
#         #polygon_str = re.sub(r" {0,}, {0,}", ',', polygon_str)

#         # print(polygon_str)
#         #points = polygon_str.split(",")
#         #poly_str = ""
#         #polygon_str = poly_str[:-1]
#         fw.write("%s,%d,\"POLYGON ((%s))\"\n" % ("filename", j, polygon_str))
#     fw.close()
    

# '''
# This function takes the contours made from pixels and map them to geo-coords.
# The mapping is computed using cordinates of its corresponding raster.
# '''
# def assign_geocoords(contours,img_path,y_flip=True):
#     dataset = rasterio.open(img_path)

#     x_min_coord = dataset.bounds[0] #left edge
#     x_max_coord = dataset.bounds[2] #right edge
#     y_min_coord = dataset.bounds[1] #bottom edge
#     y_max_coord = dataset.bounds[3] #top edge
    
#     y_img_size,x_img_size = dataset.read(1).shape
#     dataset.close()

#     for it in range(len(contours)):
#         contour = contours[it]
        
#         x = (contour[:,0])
#         y = (contour[:,1])
#         if(y_flip):
#             y = y_img_size - (y)
            
#         geo_x = x_min_coord + (x/x_img_size)*(x_max_coord - x_min_coord)
#         geo_y = y_min_coord + (y/y_img_size)*(y_max_coord - y_min_coord)

#         contours[it] = np.vstack((geo_x, geo_y)).T

#     return contours

# def polygonize(img):
#     labels = measure.label(img, connectivity=2, background=0).astype('uint16')
#     polygon_gen = shapes(labels, labels>0)
#     geoms = []
#     ct=0
#     for polygon, value in polygon_gen:
#         ct = ct+1
#         '''
#         try:
#             p = np.array(polygon['coordinates']).reshape(-1,2).astype(int)
#         except:
#             p = np.array(polygon['coordinates']).reshape(-1,2)
#             print(p)
#         '''
#         #print(p)
#         #print(p)
#         p = shape(polygon)
#         if p.area >= 0:
#             p = p.simplify(tolerance=0.5)
# #             geoms_polygons.append(p)
#             try:
#                 p = np.array(p.boundary.xy, dtype='int32').T
#             except:
#                 p = np.array(p.boundary[0].xy, dtype='int32').T

# #             pcoords_a = 1*(y_tile*sizey_new + p[:,0])
# #             pcoords_b = 1*(x_tile*sizex_new + p[:,1])
# #             p = np.vstack((pcoords_a,pcoords_b)).T
#             geoms.append(p)
#     return geoms


# from shapely.geometry import shape

# save_path = r"C:\Users\AhmadWaseem\Desktop\OUTPUT\test region_preds.npy"
# input_imgs = r"C:\Users\AhmadWaseem\Desktop\bhalli\PD-Seg Work\datasets for training - 20Z\tiff files\2017\test region.tif"
# output_dir = r"C:\Users\AhmadWaseem\Desktop\OUTPUT"

# file_name = os.path.split(save_path)[-1].split('.')[0]

# img_array = np.load(save_path)
# pix_poly = polygonize(img_array)
# geo_poly = (assign_geocoords(pix_poly, input_imgs))
# save_as_csv(output_dir, geo_poly, file_name)
# print("Done..!")
# print("Output csv file saved in: {}".format(output_dir))

# img = np.load(r"C:\Users\AhmadWaseem\Desktop\bhalli\PD-Seg Work\model v6 - DL 20Z - TS1024\output\test region_preds.npy")
# cv2.imwrite(r"C:\Users\AhmadWaseem\Desktop\bhalli\PD-Seg Work\model v6 - DL 20Z - TS1024\output\test region_preds.png", img)

True